# CIFO Project

In [ ]:
import sys
sys.path.append('..')
from copy import deepcopy
import random
from random import sample, shuffle
from statistics import stdev
import pandas as pd

In [ ]:
#import players from csv

players = pd.read_csv('../data/players.csv')
print(players)

    Unnamed: 0              Name Position  Skill  Salary (€M)
0            0       Alex Carter       GK     85           90
1            1      Jordan Smith       GK     88          100
2            2     Ryan Mitchell       GK     83           85
3            3    Chris Thompson       GK     80           80
4            4   Blake Henderson       GK     87           95
5            5     Daniel Foster      DEF     90          110
6            6     Lucas Bennett      DEF     85           90
7            7       Owen Parker      DEF     88          100
8            8      Ethan Howard      DEF     80           70
9            9        Mason Reed      DEF     82           75
10          10      Logan Brooks      DEF     86           95
11          11      Caleb Fisher      DEF     84           85
12          12     Nathan Wright      MID     92          120
13          13      Connor Hayes      MID     89          105
14          14      Dylan Morgan      MID     91          115
15      

In [16]:
names = players['Name'].tolist()
positions = players['Position'].tolist()
skills = players['Skill'].tolist()
salaries = players['Salary (€M)'].tolist()

capacity = 750
num_teams=5
team_size=7

## Sports League Optimization Solution

In [17]:
#Creating the Solution for Sports League Optimization (SLO)
from library.solution import Solution
"""Problem definition
Problem: Sports League Optimization (SLO)
Search space: All possible assignments of 35 players into 5 teams, each with 7 players (non-overlapping). Each team must be composed of: 1GK, 2DEF, 2MID, 2FWD.
Representation: List of 5 teams each one with a list of 7 players.
Fitness function: f(x)= standard deviation of the average skill rating of the teams.
Neighborhood: Swap two players with the same position between two teams.
Goal: Minimize f(x).
"""

class SLOSolution(Solution):

    def __init__(
            self,
            names: list[str]=names,
            positions : list[str]=positions,
            skills : list[int]=skills,
            salaries : list[int]=salaries,
            capacity: int = capacity,
            repr=None
    ):
        self.names = names
        self.positions = positions
        self.skills = skills
        self.salaries = salaries
        self.num_teams = num_teams
        self.team_size = team_size
        self.capacity = capacity

        if repr:
            repr = self._validate_repr(repr)

        super().__init__(repr = repr)


    #MAYBE A BETER VALIDATE FUNCTION IS NEEDED
    #--------------------------------------------------------
    def _validate_repr(self,repr):
        # Check if the representation is a list of teams
        if not isinstance(repr, list):
            raise ValueError("Representation must be a list of teams")
        #check if the number of teams is correct
        if len(repr) != self.num_teams:
            raise ValueError("Number of teams must be equal to num_teams")
        #check if each team has the correct number of players
        for team in repr:
            if not isinstance(team, list):
                raise ValueError("Each team must be a list of players")
            if len(team) != self.team_size:
                raise ValueError("Each team must have 7 players")
            

        #check if team is valid (1GK, 2DEF, 2 MID, 2FWD)
        seen_players = set()

        for i, team in enumerate(repr):
            team_positions = {'GK': 0, 'DEF': 0, 'MID': 0, 'FWD': 0}
            team_salary = 0

            seen_players = set()
            for player_idx in team:
                # Check that the player hasn't already been assigned
                if player_idx in seen_players:
                    raise ValueError(f"Player {player_idx} assigned to multiple teams")
                seen_players.add(player_idx)

                pos = self.positions[player_idx]
                sal = self.salaries[player_idx] # TO BE CONFIRMED

                if pos not in team_positions:
                    raise ValueError(f"Invalid position; '{pos}', for player {player_idx}")
                team_positions[pos] += 1 
                team_salary += sal # TO BE CONFIRMED

            
            if team_positions != {'GK': 1, 'DEF': 2, 'MID': 2, 'FWD': 2}:
                raise ValueError(f"Team {i} has invalid composition: {team_positions}")
            
            # TO BE CONFIRMED
            if team_salary > self.capacity:
                raise ValueError(f"Team {i} exceeds salary cap: {team_salary:.2f}M > {self.capacity}M")
        return repr
        
    
    def random_initial_representation(self):
        isValid=False

        while not isValid:
            indices = list(range(len(self.names)))
            random.shuffle(indices)

            repr=[]
            for i in range(0, len(self.names), self.team_size):
                team = indices[i:i + self.team_size]
                repr.append(team)

            # Check if the representation is valid
            try:
                self._validate_repr(repr)
                isValid=True
            except ValueError as e:
                print(f"Invalid representation: {e}")
                isValid=False
        return repr
                    
    def fitness(self):

        team_avg_skill=[]

        for team in self.repr:
            team_skills=[self.skills[player_idx] for player_idx in team]
            avg_skill=sum(team_skills)/len(team_skills)
            team_avg_skill.append(avg_skill)
        
        return stdev(team_avg_skill)


In [ ]:
#create a team to test the code
slo_solution = SLOSolution(
    names=names, 
    positions=positions, 
    skills=skills, 
    salaries=salaries, 
    capacity=capacity, 
    repr=None
)

random_teams = slo_solution.random_initial_representation()
print("Random teams:") 
for i, team in enumerate(random_teams):
    print(f"Team {i+1}: {[positions[player_idx] for player_idx in team]}")
    #check fitness of the repr
    print(f"Fitness: {slo_solution.fitness()}") #TO BE CONFIRMED

Invalid representation: Team 0 has invalid composition: {'GK': 0, 'DEF': 3, 'MID': 4, 'FWD': 0}
Invalid representation: Team 0 has invalid composition: {'GK': 3, 'DEF': 2, 'MID': 1, 'FWD': 1}
Invalid representation: Team 0 has invalid composition: {'GK': 1, 'DEF': 1, 'MID': 2, 'FWD': 3}
Invalid representation: Team 0 has invalid composition: {'GK': 0, 'DEF': 3, 'MID': 0, 'FWD': 4}
Invalid representation: Team 0 has invalid composition: {'GK': 1, 'DEF': 3, 'MID': 1, 'FWD': 2}
Invalid representation: Team 0 has invalid composition: {'GK': 1, 'DEF': 2, 'MID': 3, 'FWD': 1}
Invalid representation: Team 0 has invalid composition: {'GK': 1, 'DEF': 3, 'MID': 2, 'FWD': 1}
Invalid representation: Team 0 has invalid composition: {'GK': 2, 'DEF': 2, 'MID': 1, 'FWD': 2}
Invalid representation: Team 0 has invalid composition: {'GK': 1, 'DEF': 1, 'MID': 3, 'FWD': 2}
Invalid representation: Team 0 has invalid composition: {'GK': 0, 'DEF': 2, 'MID': 3, 'FWD': 2}
Invalid representation: Team 1 has inval

: 

## Mutation Functions

In [ ]:
def mutation1():
    pass

## Crossover Functions

In [ ]:
def crossover1():
    pass

## Selection Functions

In [ ]:
def selection1():
    pass

## SLO Genetic Algorithm Solution

In [ ]:
class SLOGASolution(SLOSolution):
    def __init__(
            self,
            names,
            positions,
            skills,
            salaries,
            capacity,
            mutation_function,
            crossover_function,
            repr=None,
    ):
        super().__init__(
            names=names,
            positions=positions,
            skills=skills,
            salaries=salaries,
            capacity=capacity,
            repr=repr,
        )
        self.mutation_function = mutation_function
        self.crossover_function = crossover_function
        